In [18]:
import pandas as pd
import numpy as np
from scipy.stats import randint as sp_randint

import seaborn as sns
import matplotlib.pyplot as plt

from rdkit import Chem
from rdkit.Chem import MolFromSmiles as MolFromSmiles
from rdkit.Chem.AllChem import EmbedMolecule, MMFFOptimizeMolecule


from mordred import Calculator, descriptors
import matplotlib as mpl
mpl.rcParams['figure.dpi'] = 250



In [38]:
substrates = pd.read_csv('substrates.csv')

In [40]:
smiles= list(substrates['SMILES'])
smiles

['CC(=O)C(=O)O',
 'CCC(=O)C(=O)O',
 'O=C(O)C(=O)CO',
 'CCCC(=O)C(=O)O',
 'O=C(O)C(=O)CS',
 'CC(C)(C)C(=O)C(=O)O',
 'OC(=O)C(=O)C(C)CC',
 'CC(C)CC(=O)C(=O)O',
 'O=C(O)CC(=O)C(=O)O',
 'O=C(O)C(=O)C(F)(F)F',
 'O=C(O)CCC(=O)C(=O)O',
 'CC(C)N(O)C(=O)C(O)=O',
 'CSCCC(=O)C(=O)O',
 'O=C(O)C(=O)CC(O)CO',
 'O=C(O)C(=O)c1ccccc1',
 'O=C(O)C(=O)Cc1cnc[nH]1',
 'CCCCCCC(=O)C(=O)O',
 'O=C(O)CCCC(=O)C(=O)O',
 'O=C(O)C(=O)Cc1ccccc1',
 'O=C(O)C(=O)CBr',
 'O=C(O)C(=O)Cc1ccc(O)cc1',
 'OC(=O)C(=O)CCc1cccs1',
 'O=C(O)CCCCCC(=O)C(=O)O',
 'O=C(O)C(=O)c1c[nH]c2ccccc12',
 'Cc1cc(C)c(C(=O)C(=O)O)c(C)c1',
 'OC(=O)C(=O)Cc1ccc2ccccc2n1',
 'CCOC(=O)c1csc(n1)C(C#N)C(=O)C(O)=O',
 'OC(=O)C(=O)Nc1sc2CCCCc2c1C(O)=O',
 'OC(=O)C(=O)NC1(CCCCC1)c1ccc(Cl)s1',
 'CC(=O)OC1COC(C(OC(C)=O)C1OC(C)=O)n1cc(C(=O)C(O)=O)c2ccccc12']

In [41]:
mol_list = []

from rdkit.Chem.rdchem import Mol
from rdkit.Chem import rdmolops
from rdkit.Chem import AddHs

for s in smiles:

    mol = MolFromSmiles(s)
    
    mol = AddHs(mol)
    
    #try:
    EmbedMolecule(mol)#, useRandomCoords=True)  # This calculates the 3D structure
    try:
        MMFFOptimizeMolecule(mol)  # This cleans up the 3D structure using a force field approach
    except:
        rdmolops.RemoveStereochemistry(mol)  # Structure calculations can fail if there are stereochemistry conflicts
        EmbedMolecule(mol, useRandomCoords=True)  # This calculates the 3D structure
        MMFFOptimizeMolecule(mol)  # This cleans up the 3D structure using a force field approach
    mol_list.append(mol)

In [42]:
calc = Calculator(descriptors, ignore_3D=False)

features_df = calc.pandas(mol_list, ipynb=True)

In [43]:
features_df.index = smiles
features_df.head()

ABC     ABCGG  nAcid  nBase   SpAbs_A   SpMax_A  \
CC(=O)C(=O)O    3.932653  4.244375      1      0  6.000000  2.000000   
CCC(=O)C(=O)O   4.530370  5.004088      1      0  7.662988  2.052881   
O=C(O)C(=O)CO   4.530370  5.004088      1      0  7.662988  2.052881   
CCCC(=O)C(=O)O  5.237477  5.675298      1      0  8.647053  2.074313   
O=C(O)C(=O)CS   4.530370  5.004088      1      0  7.662988  2.052881   

                SpDiam_A    SpAD_A   SpMAD_A   LogEE_A  ...     SRW10  \
CC(=O)C(=O)O    4.000000  6.000000  1.000000  2.610845  ...  7.626083   
CCC(=O)C(=O)O   4.105762  7.662988  1.094713  2.766317  ...  7.890957   
O=C(O)C(=O)CO   4.105762  7.662988  1.094713  2.766317  ...  7.890957   
CCCC(=O)C(=O)O  4.148627  8.647053  1.080882  2.900310  ...  8.011355   
O=C(O)C(=O)CS   4.105762  7.662988  1.094713  2.766317  ...  7.890957   

                   TSRW10          MW        AMW  WPath  WPol  Zagreb1  \
CC(=O)C(=O)O    30.698690   88.016044   8.801604     29     4     22.0   
CCC(=O)C(=O)O   32.688753  102.031694   7.848592     46     6     26.0   
O=C(O)C(=O)CO   32.688753  104.010959   9.455542     46     6     26.0   
CCCC(=O)C(=O)O  34.323564  116.047344   7.252959     70     7     30.0   
O=C(O)C(=O)CS   32.688753  119.988115  10.908010     46     6     26.0   

                Zagreb2  mZagreb1  mZagreb2  
CC(=O)C(=O)O       21.0  4.222222  1.444444  
CCC(=O)C(=O)O      26.0  4.472222  1.777778  
O=C(O)C(=O)CO      26.0  4.472222  1.777778  
CCCC(=O)C(=O)O     30.0  4.722222  2.027778  
O=C(O)C(=O)CS      26.0  4.472222  1.777778  

[5 rows x 1826 columns]

In [44]:
# Mordred leaves error messages in cells in df where value could not be calculated
# Replace all cells with error messages (strings) with np.nan using pd.to_numeric
features_df = features_df.apply(pd.to_numeric, errors='coerce')

features_df.to_csv('processed_data.csv')

features_df.head()

ABC     ABCGG  nAcid  nBase   SpAbs_A   SpMax_A  \
CC(=O)C(=O)O    3.932653  4.244375      1      0  6.000000  2.000000   
CCC(=O)C(=O)O   4.530370  5.004088      1      0  7.662988  2.052881   
O=C(O)C(=O)CO   4.530370  5.004088      1      0  7.662988  2.052881   
CCCC(=O)C(=O)O  5.237477  5.675298      1      0  8.647053  2.074313   
O=C(O)C(=O)CS   4.530370  5.004088      1      0  7.662988  2.052881   

                SpDiam_A    SpAD_A   SpMAD_A   LogEE_A  ...     SRW10  \
CC(=O)C(=O)O    4.000000  6.000000  1.000000  2.610845  ...  7.626083   
CCC(=O)C(=O)O   4.105762  7.662988  1.094713  2.766317  ...  7.890957   
O=C(O)C(=O)CO   4.105762  7.662988  1.094713  2.766317  ...  7.890957   
CCCC(=O)C(=O)O  4.148627  8.647053  1.080882  2.900310  ...  8.011355   
O=C(O)C(=O)CS   4.105762  7.662988  1.094713  2.766317  ...  7.890957   

                   TSRW10          MW        AMW  WPath  WPol  Zagreb1  \
CC(=O)C(=O)O    30.698690   88.016044   8.801604     29     4     22.0   
CCC(=O)C(=O)O   32.688753  102.031694   7.848592     46     6     26.0   
O=C(O)C(=O)CO   32.688753  104.010959   9.455542     46     6     26.0   
CCCC(=O)C(=O)O  34.323564  116.047344   7.252959     70     7     30.0   
O=C(O)C(=O)CS   32.688753  119.988115  10.908010     46     6     26.0   

                Zagreb2  mZagreb1  mZagreb2  
CC(=O)C(=O)O       21.0  4.222222  1.444444  
CCC(=O)C(=O)O      26.0  4.472222  1.777778  
O=C(O)C(=O)CO      26.0  4.472222  1.777778  
CCCC(=O)C(=O)O     30.0  4.722222  2.027778  
O=C(O)C(=O)CS      26.0  4.472222  1.777778  

[5 rows x 1826 columns]

In [45]:
nan_df = features_df.apply(np.isnan)
fig, ax = plt.subplots(nrows=1, ncols=1, figsize=(200, 15))

sns.heatmap(nan_df, ax=ax)

In [46]:
nan_cols = nan_df.columns[(nan_df > 0).any()]

fig, ax = plt.subplots(nrows=1, ncols=1, figsize=(100, 50))

sns.heatmap(nan_df[nan_cols], ax=ax)

In [47]:
print('Number of columns before dropping NaN columns:', len(features_df.columns))
features_df = features_df.dropna(axis=1, how='all')
print('Number of columns after dropping NaN columns:', len(features_df.columns))

Number of columns before dropping NaN columns: 1826
Number of columns after dropping NaN columns: 1697


In [48]:
features_df = features_df.fillna(0)  # Replace all np.nan values with 0

In [49]:
new_nan_df = features_df.apply(np.isnan)
assert not new_nan_df.isnull().sum().any()  # Make sure we have no np.nan values in our dataframe

In [50]:
hits = pd.read_csv('product_matrix.csv', index_col = 0)

In [51]:
hits

0             1             2             3             4  \
0   9.050506e+06  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
1   1.751321e+06  9.543539e+06  0.000000e+00  0.000000e+00  0.000000e+00   
2   5.953950e+05  2.258104e+06  7.591091e+06  0.000000e+00  0.000000e+00   
3   0.000000e+00  0.000000e+00  2.932694e+06  1.091983e+06  0.000000e+00   
4   0.000000e+00  2.473634e+07  0.000000e+00  1.219513e+06  2.944168e+06   
5   8.709787e+06  0.000000e+00  6.021113e+05  0.000000e+00  0.000000e+00   
6   5.318473e+05  6.012654e+05  4.379234e+06  0.000000e+00  3.025018e+06   
7   5.318473e+05  3.154653e+06  3.854711e+06  0.000000e+00  3.025018e+06   
8   0.000000e+00  4.065705e+06  3.091439e+06  3.460070e+06  5.190095e+06   
9   5.553935e+05  2.763210e+06  2.198916e+06  0.000000e+00  1.229187e+06   
10  5.962091e+07  8.662217e+06  8.152711e+05  2.715470e+06  0.000000e+00   
11  5.645178e+06  0.000000e+00  1.704123e+06  4.183027e+06  3.530428e+06   
12  0.000000e+00  4.653782e+06  8.579545e+07  1.338711e+06  5.781120e+05   
13  3.423224e+07  0.000000e+00  0.000000e+00  6.130532e+05  2.341636e+07   
14  1.582490e+06  4.845002e+06  1.966799e+06  1.009358e+06  8.276193e+06   
15  4.018431e+06  1.131920e+06  9.323201e+06  4.184653e+06  1.256074e+07   
16  6.199517e+06  0.000000e+00  2.233007e+06  5.152022e+06  2.187118e+07   
17  0.000000e+00  2.058370e+06  1.922651e+06  0.000000e+00  1.467041e+06   
18  4.913226e+06  0.000000e+00  1.375399e+06  1.171773e+06  0.000000e+00   
19  0.000000e+00  0.000000e+00  1.518450e+08  2.214748e+07  0.000000e+00   
20  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
21  0.000000e+00  1.017082e+06  3.413321e+06  0.000000e+00  9.324527e+05   
22  3.194995e+06  0.000000e+00  1.343544e+07  4.929063e+06  2.915074e+06   
23  8.843535e+06  5.403069e+07  1.173173e+07  1.503504e+06  5.155582e+06   
24  2.271759e+07  2.598186e+06  2.767444e+06  0.000000e+00  1.650392e+06   
25  5.427461e+07  0.000000e+00  1.888234e+07  3.033968e+06  4.630110e+07   
26  3.067463e+06  1.753594e+06  4.124350e+06  2.175862e+06  4.810857e+06   
27  2.760003e+06  1.695006e+06  1.385989e+07  1.563295e+07  2.084472e+07   
28  0.000000e+00  5.384516e+06  4.528630e+06  4.770694e+06  8.001952e+05   
29  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   

               5             6             7             8             9  ...  \
0   0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  ...   
1   0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  ...   
2   0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  ...   
3   0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  ...   
4   0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  ...   
5   1.377333e+06  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  ...   
6   0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  ...   
7   0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  ...   
8   1.119918e+06  0.000000e+00  0.000000e+00  9.432315e+06  0.000000e+00  ...   
9   1.711816e+07  1.951187e+06  2.030803e+05  0.000000e+00  4.830442e+07  ...   
10  2.837992e+05  6.901409e+05  6.901409e+05  0.000000e+00  3.037317e+06  ...   
11  8.868506e+06  1.345791e+07  4.985786e+07  1.493667e+06  4.144886e+06  ...   
12  0.000000e+00  6.536402e+05  5.476572e+05  7.889492e+05  0.000000e+00  ...   
13  1.525450e+07  2.914473e+06  5.357243e+05  0.000000e+00  3.695484e+06  ...   
14  9.338591e+05  0.000000e+00  0.000000e+00  1.422099e+06  3.741599e+06  ...   
15  9.525988e+05  5.704121e+05  5.704121e+05  6.793518e+06  4.436325e+06  ...   
16  7.334968e+05  5.493459e+05  4.625802e+05  0.000000e+00  3.322204e+05  ...   
17  0.000000e+00  7.861908e+05  0.000000e+00  1.260450e+07  1.513811e+06  ...   
18  1.223383e+06  1.726941e+06  0.000000e+00  6.726389e+06  2.638150e+06  ...   
19  0.000000e+00  7.756909e+06  0.0000

In [157]:
import random

In [195]:
features_dfx2 = pd.DataFrame()
features_dfx2_2 = pd.DataFrame()
targets=[]
test_features = pd.DataFrame()
test_targets = []
for i in range(len(smiles)):
    for j in range(i+1):
        vector1 = features_df.loc[smiles[i],:]
        vector2 = features_df.loc[smiles[j],:]
        vector2.index = vector2.index+'2'
        concat_feat = pd.DataFrame(pd.concat([vector1,vector2]))
        vector3 = features_df.loc[smiles[j],:]
        vector4 = features_df.loc[smiles[i],:]
        vector4.index = vector4.index+'2'
        concat_feat_2 = pd.DataFrame(pd.concat([vector3,vector4]))
        if random.random()>0.3:
            features_dfx2 = features_dfx2.append(concat_feat.transpose(), ignore_index=True)
            features_dfx2_2 = features_dfx2_2.append(concat_feat_2.transpose(), ignore_index=True)
            targets.append(1 if hits.iloc[i,j]>1E6 else 0)
        else:
            test_features = test_features.append(concat_feat.transpose(), ignore_index=True)
            test_targets.append(1 if hits.iloc[i,j]>1E6 else 0)

In [200]:
from sklearn.svm import SVC
from sklearn.metrics.pairwise import rbf_kernel as radial
clf = SVC(kernel='rbf', C=5, gamma=0.005, degree=3, probability=True)
comb_feats = pd.concat([features_dfx2,features_dfx2_2])
comb_targets = targets+targets
clf.fit(comb_feats, comb_targets)

SVC(C=5, break_ties=False, cache_size=200, class_weight=None, coef0=0.0,
    decision_function_shape='ovr', degree=3, gamma=0.005, kernel='rbf',
    max_iter=-1, probability=True, random_state=None, shrinking=True, tol=0.001,
    verbose=False)

In [201]:
len(targets)

333

In [202]:
len(features_dfx2)

333

In [203]:
trained=clf.predict(features_dfx2)

In [204]:
trained_2 = clf.predict(features_dfx2_2)

In [205]:
trained_test=clf.predict(test_features)

In [147]:
import numpy as np

def mean_squared_error(estimates, targets):
    """
    Mean squared error measures the average of the square of the errors (the
    average squared difference between the estimated values and what is 
    estimated. The formula is:
    MSE = (1 / n) * \sum_{i=1}^{n} (Y_i - Yhat_i)^2
    Implement this formula here, using numpy.
    https://en.wikipedia.org/wiki/Mean_squared_error
    """
    estimates = np.array(estimates)
    targets = np.array(targets)
    n = len(estimates)
    MSE= (1/n)* sum((estimates-targets)**2)
    return MSE

In [163]:
def confusion_matrix(actual, predictions):
    """
    Given predictions (an N-length numpy vector) and actual labels (an N-length 
    numpy vector), compute the confusion matrix. The confusion 
    matrix for a binary classifier would be a 2x2 matrix as follows:
    [
        [true_negatives, false_positives],
        [false_negatives, true_positives]
    ]
    YOU DO NOT NEED TO IMPLEMENT CONFUSION MATRICES THAT ARE FOR MORE THAN TWO 
    CLASSES (binary).
    
    Compute and return the confusion matrix.
    Args:
        actual (np.array): predicted labels of length N
        predictions (np.array): predicted labels of length N
    Output:
        confusion_matrix (np.array): 2x2 confusion matrix between predicted and actual labels
    """

    if predictions.shape[0] != actual.shape[0]:
        raise ValueError("predictions and actual must be the same length!")
    TP = 0
    FP = 0
    TN = 0
    FN = 0
    for i in range(len(actual)):
        if actual[i] == 1 and predictions[i] == 1:
            TP = TP+1
        if actual[i] == 0 and predictions[i] == 1:
            FP = FP + 1
        if actual[i] == 0 and predictions[i] == 0:
            TN = TN + 1
        if actual[i] == 1 and predictions[i] == 0:
            FN = FN + 1
    matrix = np.array([[TN,FP],[FN,TP]])
    return matrix

def accuracy(actual, predictions):
    """
    Given predictions (an N-length numpy vector) and actual labels (an N-length 
    numpy vector), compute the accuracy:
    Hint: implement and use the confusion_matrix function!
    Args:
        actual (np.array): predicted labels of length N
        predictions (np.array): predicted labels of length N
    Output:
        accuracy (float): accuracy
    """
    if predictions.shape[0] != actual.shape[0]:
        raise ValueError("predictions and actual must be the same length!")
    matrix = confusion_matrix(actual, predictions)
    TP = matrix[1, 1]
    TN = matrix[0, 0]
    acc = (TP+TN)/(len(actual))
    return acc

def precision_and_recall(actual, predictions):
    """
    Given predictions (an N-length numpy vector) and actual labels (an N-length 
    numpy vector), compute the precision and recall:
    https://en.wikipedia.org/wiki/Precision_and_recall
    Hint: implement and use the confusion_matrix function!
    Args:
        actual (np.array): predicted labels of length N
        predictions (np.array): predicted labels of length N
    Output:
        precision (float): precision
        recall (float): recall
    """
    if predictions.shape[0] != actual.shape[0]:
        raise ValueError("predictions and actual must be the same length!")
    matrix = confusion_matrix(actual, predictions)
    TP = matrix[1, 1]
    FP = matrix[0, 1]
    FN = matrix[1, 0]
    if TP+FP == 0:
        precision = 0
    else:
        precision = TP/(TP+FP)
    if TP+FN == 0:
        recall = 0
    else:
        recall = TP/(TP+FN)
    return precision, recall

def f1_measure(actual, predictions):
    """
    Given predictions (an N-length numpy vector) and actual labels (an N-length 
    numpy vector), compute the F1-measure:
   https://en.wikipedia.org/wiki/Precision_and_recall#F-measure
    Hint: implement and use the precision_and_recall function!
    Args:
        actual (np.array): predicted labels of length N
        predictions (np.array): predicted labels of length N
    Output:
        f1_measure (float): F1 measure of dataset (harmonic mean of precision and 
        recall)
    """
    if predictions.shape[0] != actual.shape[0]:
        raise ValueError("predictions and actual must be the same length!")

    precision, recall = precision_and_recall(actual, predictions)
    if precision == 0 and recall == 0:
        F = 0
    else:
        F = 2 * (precision * recall)/(precision + recall)
    return F

In [167]:
mean_squared_error(trained,targets)

0.0

In [192]:
accuracy(np.array(targets), np.array(trained))

0.5468277945619335

In [193]:
accuracy(np.array(targets), np.array(trained_2))

1.0

In [194]:
accuracy(np.array(test_targets), np.array(trained_test))

0.5671641791044776

In [206]:
accuracy(np.array(targets), np.array(trained))

1.0

In [207]:
accuracy(np.array(targets), np.array(trained_2))

1.0

In [208]:
accuracy(np.array(test_targets), np.array(trained_test))

0.5